In [1]:
#%pip install nltk
import nltk
from nltk.grammar import CFG, Nonterminal, PCFG
from nltk.corpus import ptb

In [2]:
print(nltk.data.path)

['/Users/sanjaya/nltk_data', '/Library/Frameworks/Python.framework/Versions/3.10/nltk_data', '/Library/Frameworks/Python.framework/Versions/3.10/share/nltk_data', '/Library/Frameworks/Python.framework/Versions/3.10/lib/nltk_data', '/usr/share/nltk_data', '/usr/local/share/nltk_data', '/usr/lib/nltk_data', '/usr/local/lib/nltk_data']


In [3]:
trainfileids = []
devfileids = []
testfileids = []

for i in range(2,25):
    subfiles = []

    for j in range(0,100):
        if( (i==3 and j>80) or (i==8 and j>20) or (i==21 and j>72) or (i==22 and j>82) or (i==24 and j>54)): #handle missing files
            break
        if i < 10:
            folder = f"0{i}"
        else:
            folder = f"{i}"

        if j < 10:
            subfolder = f"0{j}"
        else:
            subfolder = f"{j}"

        fileid = f"WSJ/{folder}/WSJ_{folder}{subfolder}.MRG"
        subfiles.append(fileid)
            
    if(i not in [23,24]):
        trainfileids.append(subfiles)
    if(i == 23):
        devfileids.append(subfiles)
    if(i == 24):
        trainfileids.append(subfiles)


In [4]:
print(ptb.words(trainfileids[0][0]))

['In', 'an', 'Oct.', '19', 'review', 'of', '``', 'The', ...]


In [5]:
print(ptb.tagged_words(trainfileids[0][0]))

[('In', 'IN'), ('an', 'DT'), ('Oct.', 'NNP'), ...]


In [35]:
ptb.parsed_sents(trainfileids[0][0])[0].draw()

In [6]:
tree = ptb.parsed_sents(trainfileids[0][0])[0]

productions = tree.productions()

#for production in productions:
    #print(production)

start_symbol = nltk.grammar.Nonterminal('S')

grammar = CFG(start_symbol, productions)

cnf_grammar = CFG.chomsky_normal_form(grammar)

for prod in CFG.productions(cnf_grammar):
    print(prod)
print()
print(CFG.start(cnf_grammar))



VP -> VBN VP@$@VBN
PRN -> -LRB- PRN@$@-LRB-
NNP -> 'Kim'
PRN@$@-LRB-@$@``@$@S-HLN -> , PRN@$@-LRB-@$@``@$@S-HLN@$@,
PP-LOC -> IN NP
PP -> IN NP
PP -> IN NP-LGS
NP-LGS -> NNP NNP
VBN -> 'attributed'
VBD -> 'was'
NP -> `` NP@$@``
PRN@$@-LRB- -> `` PRN@$@-LRB-@$@``
NP-SBJ-2@$@NP -> , NP-SBJ-2@$@NP@$@,
DT -> 'the'
NNS -> 'Arts'
NP -> 'Theatre'
NN -> 'review'
VBP -> 'Take'
NP@$@`` -> NP-TTL NP@$@``@$@NP-TTL
POS -> "'s"
NN -> 'Stage'
NP-TTL -> DT NN
-RRB- -> '-RRB-'
S@$@PP-LOC@$@, -> NP-SBJ-2 S@$@PP-LOC@$@,@$@NP-SBJ-2
NP-TMP@$@NN -> CC NNS
NNS -> 'Classics'
PRN@$@-LRB-@$@``@$@S-HLN@$@, -> '' PRN@$@-LRB-@$@``@$@S-HLN@$@,@$@''
IN -> 'of'
RB -> 'mistakenly'
VP -> VBD VP
DT -> 'The'
-LRB- -> '-LRB-'
NP -> '*'
VP -> ADVP-MNR VP@$@ADVP-MNR
PP-CLR -> TO NP
PRN@$@-LRB-@$@`` -> S-HLN PRN@$@-LRB-@$@``@$@S-HLN
NN -> 'Leisure'
NP -> 'Haag'
-NONE- -> '*-2'
NP -> 'City'
NP@$@DT -> NNP NP@$@DT@$@NNP
S@$@PP-LOC -> , S@$@PP-LOC@$@,
IN -> 'In'
CC -> '&'
NP@$@``@$@NP-TTL -> '' PP-LOC
NNP -> 'Haag'
NNP -> 'City

In [56]:
productions = []

for foldernum in range(0,len(trainfileids)):
    for mrgfile in trainfileids[foldernum]:
        for x in ptb.parsed_sents(mrgfile):
            x.collapse_unary(collapsePOS = False)
            x.chomsky_normal_form(horzMarkov = 2)
            productions += x.productions()


In [57]:
pgrammar = nltk.induce_pcfg(Nonterminal('S'), productions)

"""I tried converting this to a standard cnf using nltk's library, but it took a very long time (and crashed my kernel)"""
#cnf_pgrammar = pgrammar.chomsky_normal_form()
#print(cnf_pgrammar)

print(pgrammar)

: 

In [43]:
print(nltk.grammar.PCFG.is_flexible_chomsky_normal_form(pgrammar))

ii = 4

print(pgrammar.productions()[ii])
print(pgrammar.productions()[ii].lhs())
print(pgrammar.productions()[ii].rhs())
print(pgrammar.productions()[ii].prob())


True
NP -> DT NP|<NNP-CD> [0.000413915]
NP
(DT, NP|<NNP-CD>)
0.0004139154429880753


In [52]:
grammar_dict = {}

for prod in pgrammar.productions():

    lhs = prod.lhs().symbol() 
    rhs = tuple(str(s) for s in prod.rhs())
    prob = prod.prob()

    if lhs not in grammar_dict:
        grammar_dict[lhs] = []

    grammar_dict[lhs].append((rhs, prob))

for key, value in grammar_dict.items():
    print(key, " -> ", value)

S  ->  [(('PP-LOC', 'S|<,-NP-SBJ-2>'), 0.000277736236033072), (('NP-SBJ', 'S|<VP-.>'), 0.17076505650864188), (('NP-SBJ', 'VP'), 0.3882645758113103), (('NP-SBJ', 'S|<NP-TMP-VP>'), 0.0013139060396949174), (('NP-SBJ-1', 'S|<VP-.>'), 0.033937231610656524), (('S-TPC-1', 'S|<,-NP-SBJ>'), 0.0060140577264084435), (('-NONE-',), 0.053271946503728074), (('PP-LOC', 'S|<,-NP-SBJ>'), 0.008438908710235648), (('NP-SBJ', 'S|<ADVP-VP>'), 0.01426068750400581), (('S', 'S|<:-CC>'), 0.0005982011237635396), (('NP-SBJ-3', 'S|<ADVP-TMP-VP>'), 0.00012818595509218707), (('NP-SBJ-2', 'VP'), 0.024013502253936378), (('``', 'S|<ADVP-NP-SBJ>'), 9.61394663191403e-05), (('ADVP-TMP', 'S|<,-NP-SBJ>'), 0.0030764629222124894), (('CC', 'S|<NP-SBJ-,>'), 0.00016023244386523383), (('NP-SBJ-1', 'S|<``-VP>'), 0.000277736236033072), (('SBAR-NOM-SBJ', 'S|<VP-.>'), 0.0004913794945200505), (('PP', 'S|<,-NP-SBJ>'), 0.011643557587540326), (('NP-SBJ-3', 'VP'), 0.008887559553058304), (('S-ADV', 'S|<PRN-NP-SBJ-1>'), 1.0682162924348922e-0

comparing to original example grammar that i used when making CKY

{'S': [(('NP', 'VP'), 0.8), (('VP', 'NP'), 0.2)], 'NP': [(('D', 'N'), 0.8), (('NP', 'NP'), 0.2)], 'VP': [(('V', 'P'), 1)], 'D': [('the', 1)], 'N': [('woman', 0.6), ('man', 0.4)], 'V': [('saw', 1)], 'P': [('him', 1)]

{'S': [(('PP-LOC', 'S|<,-NP-SBJ-2>'), 0.000277736236033072)], 'PP-LOC': [(('IN', 'NP'), 0.9514482965631097)], 'IN': [(('In',), 0.017656697302998344)], 'NP': [(('NP', 'NP|<PP-PRN>'), 0.00014585591800532176), (('DT', 'NP|<NNP-CD>'), 0.0004139154429880753)], 'DT': [(('an',), 0.03781927014250246)]}